In [1]:
import plotly.express as px
from shapely.geometry import Polygon, MultiPolygon
import geopandas as gpd
import matplotlib.pyplot as plt
import geojsoncontour

In [2]:
import pandas as pd
import numpy as np
import re
import json
from datetime import datetime

from scipy.interpolate import griddata
from numpy import linspace

In [3]:
from IPython.display import HTML
HTML('''<script>
code_show=true; 
function code_toggle() {
 if (code_show){
 $('div.input').hide();
 } else {
 $('div.input').show();
 }
 code_show = !code_show
} 
$( document ).ready(code_toggle);
</script>
The raw code for this IPython notebook is by default hidden for easier reading.
To toggle on/off the raw code, click <a href="javascript:code_toggle()">here</a>.''')

In [4]:
# Cufflinks wrapper on plotly
import cufflinks
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = 'all'

from plotly.offline import iplot
cufflinks.go_offline()

# Set global theme

import plotly.figure_factory as ff

import plotly.graph_objects as go
#Selecting a central city point to center all graphs around - Swietokrzyska Subway 
center_coors=52.235176, 21.008393

In [5]:
import random
import warnings
warnings.filterwarnings("ignore")

In [6]:
df = pd.read_excel(r"https://raw.githubusercontent.com/Jan-Majewski/Project_Portfolio/master/03_Real_Estate_pricing_in_Warsaw/RE_models_input_enriched.xlsx")

In [7]:
df.columns

Index(['Id', 'Area', 'Price', 'latitude', 'longitude', 'build_year',
       'building_floors_num', 'rooms_num', 'City', 'subdistrict', 'market',
       'Building_material', 'Building_ownership', 'Building_type',
       'Construction_status', 'floor_no', 'Heating', 'Windows_type',
       'Equipment_types_dishwasher', 'Equipment_types_fridge',
       'Equipment_types_furniture', 'Equipment_types_oven',
       'Equipment_types_stove', 'Equipment_types_tv',
       'Equipment_types_washing_machine', 'Extras_types_air_conditioning',
       'Extras_types_attic', 'Extras_types_balcony', 'Extras_types_basement',
       'Extras_types_garage', 'Extras_types_garden', 'Extras_types_lift',
       'Extras_types_separate_kitchen', 'Extras_types_terrace',
       'Extras_types_two_storey', 'Extras_types_usable_room',
       'Media_types_cable-television', 'Media_types_electricity',
       'Media_types_internet', 'Media_types_phone', 'Media_types_sewage',
       'Media_types_water', 'Security_types_alarm

In [8]:
base_columns=['Id', 'Area', 'Price', 'latitude', 'longitude', 'build_year',
       'market', 'district', 'unit_price', 'lon_mod', 'lat_mod', 'grid_price',
       'sample_size', 'distance_transit_8AM', 'time_transit_8AM',
       'distance_driving_8AM', 'time_driving_8AM',
       'distance_return_transit_5PM', 'time_return_transit_5PM',
       'distance_return_driving_5PM', 'time_return_driving_5PM',
       'restaurant_price_level', 'restaurant_mean_rating',
       'restaurant_mean_popularity', 'restaurant_count']

In [9]:
df=df[base_columns]

In [10]:
df.shape

(11788, 25)

In [11]:
df_map=df.groupby(['lon_mod', 'lat_mod'],as_index=False).mean()

In [12]:
df_map.head()

lon_mod  lat_mod            Id       Area          Price   latitude  \
0   20.835  52.1925  6.044696e+07  36.000000  299000.000000  52.191268   
1   20.850  52.1925  6.045811e+07  54.970000  459000.000000  52.189112   
2   20.850  52.2000  6.044745e+07  67.066667  635000.000000  52.198456   
3   20.865  52.1850  6.048529e+07  65.059310  515701.655172  52.187444   
4   20.865  52.1925  6.043365e+07  62.745000  508247.090909  52.192833   

   longitude   build_year   unit_price   grid_price  ...  \
0  20.832606  2012.000000  8305.000000  8305.000000  ...   
1  20.849917  1974.000000  8349.500000  8349.500000  ...   
2  20.856400  2013.333333  9515.000000  9515.000000  ...   
3  20.869715  2014.034483  7998.482759  7998.482759  ...   
4  20.866064  2000.454545  8062.136364  8062.136364  ...   

   distance_driving_8AM  time_driving_8AM  distance_return_transit_5PM  \
0                14.700         27.666667                       15.242   
1                14.003         27.250000                       14.836   
2                12.568         25.316667                       13.661   
3                13.200         24.016667                       12.362   
4                12.482         26.000000                       11.774   

   time_return_transit_5PM  distance_return_driving_5PM  \
0                50.250000                       18.236   
1                48.266667                       14.866   
2                52.416667                       12.571   
3                39.900000                       12.917   
4                32.833333                       13.483   

   time_return_driving_5PM  restaurant_price_level  restaurant_mean_rating  \
0                24.150000                     1.5                   3.350   
1                23.216667                     1.5                   3.350   
2                23.633333                     1.5                   3.350   
3                21.383333                     1.5                   3.350   
4                22.150000                     1.6                   4.425   

   restaurant_mean_popularity  restaurant_count  
0                  201.166667               6.0  
1                  201.166667               6.0  
2                  201.166667               6.0  
3                  201.166667               6.0  
4                  205.500000               8.0  

[5 rows x 23 columns]

In [13]:
df_map.columns

Index(['lon_mod', 'lat_mod', 'Id', 'Area', 'Price', 'latitude', 'longitude',
       'build_year', 'unit_price', 'grid_price', 'sample_size',
       'distance_transit_8AM', 'time_transit_8AM', 'distance_driving_8AM',
       'time_driving_8AM', 'distance_return_transit_5PM',
       'time_return_transit_5PM', 'distance_return_driving_5PM',
       'time_return_driving_5PM', 'restaurant_price_level',
       'restaurant_mean_rating', 'restaurant_mean_popularity',
       'restaurant_count'],
      dtype='object')

# Dividing data into deciles

In [14]:
# Highest values should receive top score
normal_buckets=['restaurant_price_level',
       'restaurant_mean_rating', 'restaurant_mean_popularity',
       'restaurant_count','build_year']

In [15]:
normal_labels=np.ones([100,])
for i in range(0,normal_labels.shape[0]):
    normal_labels[i]=i+1

In [16]:
# Lowest values should receive top score
reversed_buckets=['unit_price','distance_transit_8AM', 'time_transit_8AM', 'distance_driving_8AM',
       'time_driving_8AM', 'distance_return_transit_5PM',
       'time_return_transit_5PM', 'distance_return_driving_5PM',
       'time_return_driving_5PM',"Price","Area"]

In [17]:
reversed_labels=np.ones([100,])
for i in range(0,reversed_labels.shape[0]):
    reversed_labels[i]=normal_labels[99-i]


In [18]:
noise=np.random.rand(df_map.shape[0],df_map.shape[1]-3)/10000

In [19]:
df_map.iloc[:,3:]=df_map.iloc[:,3:]+noise

In [20]:
df_dec=df_map.iloc[:,:3]

In [21]:
bin_count=10

for feature in normal_buckets:
    df_dec[feature]=pd.qcut(df_map[feature],100,labels=normal_labels).astype(int)
    
for feature in reversed_buckets:
    df_dec[feature]=pd.qcut(df_map[feature],100,labels=reversed_labels).astype(int)

In [22]:
df_dec["filter_unit_price"]=df_map.unit_price
df_dec["filter_transit_time"]=(df_map.time_transit_8AM+df_map.time_return_transit_5PM)/2
df_dec["filter_driving_time"]=(df_map.time_driving_8AM+df_map.time_return_driving_5PM)/2
df_dec["filter_distance"]=df_map.distance_driving_8AM

# Creating key KPIs

## Transport KPI

In [23]:
car_ratio=0.2
commute_ratio=1-car_ratio

In [24]:
df_dec["KPI_transport"]=df_dec.time_driving_8AM*car_ratio+df_dec.time_transit_8AM*commute_ratio

## Culture KPI

In [25]:
restaurant_popularity_share=0.2
restaurant_rating_share=0.3
restaurant_count_share=0.4
restaurant_price_share=1-restaurant_popularity_share-restaurant_rating_share-restaurant_count_share

In [26]:
df_dec["KPI_Culture"]=df_dec.restaurant_mean_popularity*restaurant_popularity_share\
                        +df_dec.restaurant_mean_rating*restaurant_rating_share\
                        +df_dec.restaurant_count*restaurant_count_share\
                        +df_dec.restaurant_price_level*restaurant_price_share

## Price KPI

In [27]:
unit_price_ratio=1
abs_price_ratio=1-unit_price_ratio

In [28]:
df_dec["KPI_Price"]=df_dec.unit_price*unit_price_ratio+df_dec.Price*abs_price_ratio

In [29]:
df_dec[["KPI_Price","KPI_transport","KPI_Culture"]]

KPI_Price  KPI_transport  KPI_Culture
0           76            7.0         21.7
1           75            4.0         26.3
2           56            6.0         29.1
3           81           31.2         36.3
4           81           15.0         78.5
..         ...            ...          ...
405         77           11.2         27.7
406         74           27.8         85.5
407         75           12.8         39.5
408         70           10.4         27.3
409         81           16.4         30.5

[410 rows x 3 columns]

# Visualizing optimal area

In [30]:
def create_geojson(x,y,z, rescale):
    xi = linspace(x.min(),x.max(),50);
    yi = linspace(y.min(),y.max(),50);
    zi = griddata((x, y), z, (xi[None,:], yi[:,None]), method="linear")

   
    cs = plt.contourf(xi,yi,zi,range(int(np.nanmin(zi)),int(np.nanmax(zi))+5,5),cmap=plt.cm.jet)
    plt.close()
    
    
    
    

    geojson = geojsoncontour.contourf_to_geojson(
    contourf=cs,
    ndigits=3,
   
    )

    json_dict=eval(geojson)
    
    arr_temp=np.ones([len(json_dict["features"]),2])
    
    for i in range(0, len(json_dict["features"])):
        json_dict["features"][i]["id"]=i

    
        arr_temp[i,0]=i
        arr_temp[i,1]=float(json_dict["features"][i]["properties"]["title"])/rescale
    
    df_contour=pd.DataFrame(arr_temp, columns=["Id","value"])
   
    
    return(json_dict, df_contour)

In [31]:
def plot_geojson_countour(geojson, df, title):
    trace = go.Choroplethmapbox(
                                geojson=geojson,
                                locations=df.Id,
                                z=df.value,
                                colorscale="jet",
                                zauto=False,
                                zmax=5,


                                marker_line_width=0,

                                marker=dict(opacity=0.5),

                               )
    layout = go.Layout(
        title=title,




        height = 800,
        # top, bottom, left and right margins
        margin = dict(t = 80, b = 0, l = 0, r = 0),
        font = dict(color = 'dark grey', size = 18),

        mapbox = dict(


            center = dict(
                lat = center_coors[0],
                lon = center_coors[1]
            ),
            # default level of zoom
            zoom = 10,
            # default map style
            style = "carto-positron"
        )

    )

    figure=dict(
        data=[trace],
        layout=layout,


        )

    iplot(figure)

In [32]:
json_dict_price, df_contour_price=create_geojson(df_dec.lon_mod,df_dec.lat_mod,df_dec.KPI_Price,20)

In [33]:
plot_geojson_countour(json_dict_price, df_contour_price, "Price KPI heatmap")

In [34]:
json_dict_transport, df_contour_transport=create_geojson(df_dec.lon_mod,df_dec.lat_mod,df_dec.KPI_transport,20)

In [35]:
plot_geojson_countour(json_dict_transport, df_contour_transport, "Transport Heatmap")

In [36]:
json_dict_culture, df_contour_culture=create_geojson(df_dec.lon_mod,df_dec.lat_mod,df_dec.KPI_Culture,20)

In [37]:
plot_geojson_countour(json_dict_culture, df_contour_culture, "Culture Heatmap")

# Final score

## Scenarion A: Classic Kowalski
 - Median wage employee
 - High price sensivity
 - Prefers transport by car
 - Low interested in culture and dining out
 - Budget cap of 10k/m2
 - Drivetime cap of 30 mins

 


In [38]:
price_share=0.7
transport_share=0.2
culture_share=1-price_share-transport_share

In [39]:
df_dec["KPI_Summary"]=df_dec.KPI_Price*price_share+df_dec.KPI_transport*transport_share+df_dec.KPI_Culture*culture_share

In [40]:
json_dict_summary, df_contour_summary=create_geojson(df_dec.lon_mod,df_dec.lat_mod,df_dec.KPI_Summary,20)

In [41]:
plot_geojson_countour(json_dict_summary, df_contour_summary, "Optimal location")

### Filter by price

In [42]:
price_limit=10000

In [43]:
df_dec["KPI_Summary"]=np.where(df_dec.filter_unit_price<=price_limit,df_dec.KPI_Summary,np.NaN)

In [44]:
json_dict_summary, df_contour_summary=create_geojson(df_dec.lon_mod,df_dec.lat_mod,df_dec.KPI_Summary,20)

In [45]:
plot_geojson_countour(json_dict_summary, df_contour_summary, "Optimal location within budget")

### Filter by drivetime to center

In [46]:
drivetime_limit=30

In [47]:
df_dec["KPI_Summary"]=np.where(df_dec.filter_driving_time<=drivetime_limit,df_dec.KPI_Summary,np.NaN)

In [48]:
json_dict_summary, df_contour_summary=create_geojson(df_dec.lon_mod,df_dec.lat_mod,df_dec.KPI_Summary,20)

In [49]:
plot_geojson_countour(json_dict_summary, df_contour_summary, "Optimal location within budget and drivetime")

## Scenario B: Aspiring professional
 - High wage
 - Low price sensivity
 - High focus on short commute to work
 - High interested in culture and dining out
 - Budget cap of 15k/m2
 - Drivetime cap of 15 mins


In [50]:
price_share=0.3
transport_share=0.5
culture_share=1-price_share-transport_share

In [51]:
df_dec["KPI_Summary"]=df_dec.KPI_Price*price_share+df_dec.KPI_transport*transport_share+df_dec.KPI_Culture*culture_share

In [52]:
json_dict_summary, df_contour_summary=create_geojson(df_dec.lon_mod,df_dec.lat_mod,df_dec.KPI_Summary,20)

In [53]:
plot_geojson_countour(json_dict_summary, df_contour_summary, "Optimal location")

### Filter by price

In [54]:
price_limit=15000

In [55]:
df_dec["KPI_Summary"]=np.where(df_dec.filter_unit_price<=price_limit,df_dec.KPI_Summary,np.NaN)

In [56]:
json_dict_summary, df_contour_summary=create_geojson(df_dec.lon_mod,df_dec.lat_mod,df_dec.KPI_Summary,20)

In [57]:
plot_geojson_countour(json_dict_summary, df_contour_summary, "Optimal location within budget")

### Filter by drivetime to center

In [58]:
drivetime_limit=20

In [59]:
df_dec["KPI_Summary"]=np.where(df_dec.filter_driving_time<=drivetime_limit,df_dec.KPI_Summary,np.NaN)

In [60]:
json_dict_summary, df_contour_summary=create_geojson(df_dec.lon_mod,df_dec.lat_mod,df_dec.KPI_Summary,20)

In [61]:
plot_geojson_countour(json_dict_summary, df_contour_summary, "Optimal location within budget and drivetime")